In [2]:
import pandas as pd

import plotly.graph_objects as go

import numpy as np

import plotly.express as px

df = pd.read_csv(r"C:\Users\samue\OneDrive\Documents\GitHub\captain_planet_sammy\captain-planet\data\clean\datos_clean.csv", encoding = "latin")
df[["fecha_de_recepcion", "fecha_de_ratificacion", "fecha_de_turno", "fecha_de_admision/radicacion", "fecha_de_conclusion"]] = df[["fecha_de_recepcion", "fecha_de_ratificacion", "fecha_de_turno", "fecha_de_admision/radicacion", "fecha_de_conclusion"]].apply(pd.to_datetime, errors = 'coerce')


C:\Users\samue\AppData\Local\Temp\ipykernel_12172\1226273309.py:9: DtypeWarning: Columns (21) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(r"C:\Users\samue\OneDrive\Documents\GitHub\captain_planet_sammy\captain-planet\data\clean\datos_clean.csv", encoding = "latin")
c:\Users\samue\OneDrive\Escritorio\Verano 2022\venv_sabueso\env\lib\site-packages\pandas\core\tools\datetimes.py:1047: UserWarning: Parsing '30/01/2002' in DD/MM/YYYY format. Provide format or specify infer_datetime_format=True for consistent parsing.
  cache_array = _maybe_cache(arg, format, cache, convert_listlike)
c:\Users\samue\OneDrive\Escritorio\Verano 2022\venv_sabueso\env\lib\site-packages\pandas\core\tools\datetimes.py:1047: UserWarning: Parsing '29/04/2002' in DD/MM/YYYY format. Provide format or specify infer_datetime_format=True for consistent parsing.
  cache_array = _maybe_cache(arg, format, cache, convert_listlike)
c:\Users\samue\OneDrive\Escritorio\Verano 2022\

In [11]:


import pandas as pd

from simpledbf import Dbf5

dbf = Dbf5(r'C:\Users\samue\OneDrive\Documents\GitHub\captain_planet_sammy\captain-planet\data\raw\ri_11.dbf')

df_pob = dbf.to_dataframe()



def correlacion_densidad_parametro(columna, parametro):

    #dataframe vacio
    df_comparativo = pd.DataFrame(columns=['colonia', 'num_denuncias','hab_por_km_cuadrado'], index = range(df['colonia'].unique().size))

    #iniciar indice
    index = 0
    
    for colonia in df['colonia'].unique():
        

        #checar q la colina exista en la base de densidad
        if(colonia.upper() in df_pob['colonia'].unique()):

            #asignar colonia
            df_comparativo.iloc[index, 0] = colonia

            #numero de denuncias por colonia siguiendo parametro de columna dados
            df_comparativo.iloc[index,1] =  df[(df[columna]==parametro) & (df['colonia']==colonia)].shape[0]
            
            #& (df['fecha_de_recepcion'].dt.year == 2010) se reducen demasiado los resultados

            #datos especificos de la colonia (en tabla densidad)
            datos_colonia = df_pob[df_pob['colonia'] == colonia.upper()]

            if(not datos_colonia.empty):
                #densidad x km cuadrado
                df_comparativo.iloc[index,2] = (1000000/int(datos_colonia.iloc[0,5])*int(datos_colonia.iloc[0,4]))
            

      
        
        index = index +1 
        
        

    return df_comparativo.dropna()


correlacion_densidad_parametro('materia', 'Maltrato Animal')




colonia num_denuncias hab_por_km_cuadrado
2               San Rafael            55        17504.588062
5                 Santa Fe            24         3472.985429
6     Fuentes del Pedregal            10         2141.587003
19            Los Cipreses             9         5272.258456
20        Lorenzo Boturini             7          16199.8044
...                    ...           ...                 ...
1625      Tres Mosqueteros             1        15420.424789
1629        La Guadalupana             1         6222.409647
1642               La Mesa             0         6346.888613
1644           Tecacalanco             2          763.733566
1647              Taxqueña             0        17092.565866

[508 rows x 3 columns]

Pruebas iniciales de mergear datasets, sin linkage

In [9]:
df_pob[df_pob['colonia']=='SAN RAFAEL']

cve_ent      alcaldia cve_col     colonia  pob_2010  SUP_COL_M2  VIV2010  \
70      09  AZCAPOTZALCO  02-086  SAN RAFAEL    2127.0    121511.0      626   

    DENVIVHa  SUPMNZHa  C_DENVIVHa  
70    51.518   12.1511           3

In [85]:
correlacion_materias = pd.DataFrame(columns=['materia','correlacion_con_densidad'], index = range(df['materia'].unique().size))

index = 0
for materia in df['materia'].unique():
    tabla_denuncias_densidad = correlacion_densidad_parametro('materia', materia)
    correlacion_materias.iloc[index, 0] = materia
    correlacion_materias.iloc[index, 1] = tabla_denuncias_densidad['num_denuncias'].astype('float64').corr(tabla_denuncias_densidad['hab_por_km_cuadrado'].astype('float64'))
    index = index + 1


# se logro :) la tabla con correlaciones de materia con densidad de poblacion
correlacion_materias.head(50)



materia correlacion_con_densidad
0    Áreas Verdes (en Suelo Urbano)                -0.231237
1             Suelo de Conservación                 0.022309
2                              Aire                -0.086088
3                   Maltrato Animal                 0.026418
4               Uso de Suelo Urbano                -0.206117
5               Ruido y Vibraciones                -0.090537
6                          Residuos                -0.128388
7                         Barrancas                 -0.11943
8                              Agua                 -0.11773
9           Gases, Olores y Vapores                -0.078765
10         Áreas de Valor Ambiental                  -0.1856
11             Contaminación Visual                -0.132053
12                 Energía Lumínica                -0.033685
13       Áreas Naturales Protegidas                -0.177687
14       Construcciones Irregulares                -0.209894
15                            Ruido                -0.065138
16         Emisiones a la Atmósfera                -0.011643
17    Contravención al Uso de Suelo                -0.090981
18  Contravención a la Zonificación                -0.079574
19       Afectación de Áreas Verdes                -0.071753
20           Afectación al Arbolado                -0.075867
21                      Vibraciones                -0.007173
22                         Anuncios                -0.065383

In [87]:
correlacion_materias.to_csv(r'C:\Users\samue\OneDrive\Documents\GitHub\captain_planet_sammy\captain-planet\data\clean\correlacion_materia_densidad.csv', encoding = 'latin')

In [95]:
#para presentarlo al equipo

correlacion_materias = pd.read_csv(r'C:\Users\samue\OneDrive\Documents\GitHub\captain_planet_sammy\captain-planet\data\clean\correlacion_materia_densidad.csv', encoding = 'latin', index_col= 0)
correlacion_materias

materia  correlacion_con_densidad
0    Áreas Verdes (en Suelo Urbano)                 -0.231237
1             Suelo de Conservación                  0.022309
2                              Aire                 -0.086088
3                   Maltrato Animal                  0.026418
4               Uso de Suelo Urbano                 -0.206117
5               Ruido y Vibraciones                 -0.090537
6                          Residuos                 -0.128388
7                         Barrancas                 -0.119430
8                              Agua                 -0.117730
9           Gases, Olores y Vapores                 -0.078765
10         Áreas de Valor Ambiental                 -0.185600
11             Contaminación Visual                 -0.132053
12                 Energía Lumínica                 -0.033685
13       Áreas Naturales Protegidas                 -0.177687
14       Construcciones Irregulares                 -0.209894
15                            Ruido                 -0.065138
16         Emisiones a la Atmósfera                 -0.011643
17    Contravención al Uso de Suelo                 -0.090981
18  Contravención a la Zonificación                 -0.079574
19       Afectación de Áreas Verdes                 -0.071753
20           Afectación al Arbolado                 -0.075867
21                      Vibraciones                 -0.007173
22                         Anuncios                 -0.065383